In [201]:
!pip install transformers

In [202]:
!pip install --upgrade accelerate

In [203]:
import accelerate


In [204]:
!pip uninstall accelerate transformers -y
!pip install transformers torch torchtext torchvision

Found existing installation: accelerate 0.30.0
Uninstalling accelerate-0.30.0:
  Successfully uninstalled accelerate-0.30.0
Found existing installation: transformers 4.40.2
Uninstalling transformers-4.40.2:
  Successfully uninstalled transformers-4.40.2
  Using cached transformers-4.40.2-py3-none-any.whl (9.0 MB)


In [1]:
pip install datasets

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


from google.colab import drive
drive.mount('/content/drive')

In [3]:
!pip install evaluate

In [4]:
pip install 'transformers[torch]'

  Using cached accelerate-0.30.0-py3-none-any.whl (302 kB)


In [5]:
import torch
import torchtext
import re
import nltk
#from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer

In [6]:
import pandas as pd
df=pd.read_json(f"/content/drive/My Drive/NLP_group_project/training_data/train.json", orient='records')
dev=pd.read_json(f"/content/drive/My Drive/NLP_group_project/training_data/dev.json", orient='records')
test=pd.read_json(f"/content/drive/My Drive/NLP_group_project/test.json", orient='records')

In [7]:
df=df.T
dev=dev.T
test=test.T

In [11]:
import pandas as pd
import json


df['Primary Interventions'] = ''
df['Primary Eligibility'] = ''
df['Primary Results'] = ''
df['Primary Adverse Events'] = ''
df['Secondary Interventions'] = ''
df['Secondary Eligibility'] = ''
df['Secondary Results'] = ''
df['Secondary Adverse Events'] = ''


dev['Primary Interventions'] = ''
dev['Primary Eligibility'] = ''
dev['Primary Results'] = ''
dev['Primary Adverse Events'] = ''
dev['Secondary Interventions'] = ''
dev['Secondary Eligibility'] = ''
dev['Secondary Results'] = ''
dev['Secondary Adverse Events'] = ''

test['Primary Interventions'] = ''
test['Primary Eligibility'] = ''
test['Primary Results'] = ''
test['Primary Adverse Events'] = ''
test['Secondary Interventions'] = ''
test['Secondary Eligibility'] = ''
test['Secondary Results'] = ''
test['Secondary Adverse Events'] = ''



def extract_info_from_json(file_path):
    with open(file_path, 'r') as file:
        data = json.load(file)

    interventions = data.get("Intervention", 'Not Available')
    eligibility_criteria = data.get("Eligibility", 'Not Available')
    results = data.get("Results", 'Not Available')
    adverse_events = data.get('Adverse Events','Not Available')
    return interventions, eligibility_criteria, results, adverse_events


for index, row in df.iterrows():
    primary_file_path = f"/content/drive/My Drive/NLP_group_project/training_data/CT json/{row['Primary_id']}.json"
    secondary_file_path = f"/content/drive/My Drive/NLP_group_project/training_data/CT json/{row['Secondary_id']}.json"

    primary_interventions, primary_eligibility, primary_results, primary_adverse_events  = extract_info_from_json(primary_file_path)


    df.at[index, 'Primary Interventions'] = primary_interventions
    df.at[index, 'Primary Eligibility'] = primary_eligibility
    df.at[index, 'Primary Results'] = primary_results
    df.at[index, 'Primary Adverse Events'] = primary_adverse_events

    if pd.notnull(row['Secondary_id']):
        secondary_interventions, secondary_eligibility, secondary_results, secondary_adverse_events = extract_info_from_json(secondary_file_path)
        df.at[index, 'Secondary Interventions'] = secondary_interventions
        df.at[index, 'Secondary Eligibility'] = secondary_eligibility
        df.at[index, 'Secondary Results'] = secondary_results
        df.at[index, 'Secondary Adverse Events'] = secondary_adverse_events

for index, row in dev.iterrows():


    primary_file_path = f"/content/drive/My Drive/NLP_group_project/training_data/CT json/{row['Primary_id']}.json"
    secondary_file_path = f"/content/drive/My Drive/NLP_group_project/training_data/CT json/{row['Secondary_id']}.json"

    primary_interventions, primary_eligibility, primary_results, primary_adverse_events  = extract_info_from_json(primary_file_path)


    dev.at[index, 'Primary Interventions'] = primary_interventions
    dev.at[index, 'Primary Eligibility'] = primary_eligibility
    dev.at[index, 'Primary Results'] = primary_results
    dev.at[index, 'Primary Adverse Events'] = primary_adverse_events

    if pd.notnull(row['Secondary_id']):
        secondary_interventions, secondary_eligibility, secondary_results, secondary_adverse_events = extract_info_from_json(secondary_file_path)
        dev.at[index, 'Secondary Interventions'] = secondary_interventions
        dev.at[index, 'Secondary Eligibility'] = secondary_eligibility
        dev.at[index, 'Secondary Results'] = secondary_results
        dev.at[index, 'Secondary Adverse Events'] = secondary_adverse_events

for index, row in test.iterrows():
    primary_file_path = f"/content/drive/My Drive/NLP_group_project/training_data/CT json/{row['Primary_id']}.json"
    secondary_file_path = f"/content/drive/My Drive/NLP_group_project/training_data/CT json/{row['Secondary_id']}.json"

    primary_interventions, primary_eligibility, primary_results, primary_adverse_events  = extract_info_from_json(primary_file_path)

    test.at[index, 'Primary Interventions'] = primary_interventions
    test.at[index, 'Primary Eligibility'] = primary_eligibility
    test.at[index, 'Primary Results'] = primary_results
    test.at[index, 'Primary Adverse Events'] = primary_adverse_events

    if pd.notnull(row['Secondary_id']):
        secondary_interventions, secondary_eligibility, secondary_results, secondary_adverse_events = extract_info_from_json(secondary_file_path)
        test.at[index, 'Secondary Interventions'] = secondary_interventions
        test.at[index, 'Secondary Eligibility'] = secondary_eligibility
        test.at[index, 'Secondary Results'] = secondary_results
        test.at[index, 'Secondary Adverse Events'] = secondary_adverse_events





In [12]:
def set_evidence(row):
    if row['Section_id'] == 'Intervention':

        if pd.isna(row['Secondary_id']):

            row['primary_evidence'] = row['Primary Interventions']
            row['secondary_evidence'] = None

            row['primary_evidence'] = row['Primary Interventions']
            row['secondary_evidence'] = row['Secondary Interventions']
    elif row['Section_id'] == 'Eligibility':

        if pd.isna(row['Secondary_id']):

            row['primary_evidence'] = row['Primary Eligibility']
            row['secondary_evidence'] = None
        else:

            row['primary_evidence'] = row['Primary Eligibility']
            row['secondary_evidence'] = row['Secondary Eligibility']
    elif row['Section_id'] == 'Results':
        if pd.isna(row['Secondary_id']):

            row['primary_evidence'] = row['Primary Results']
            row['secondary_evidence'] = None
        else:

            row['primary_evidence'] = row['Primary Results']
            row['secondary_evidence'] = row['Secondary Results']
    elif row['Section_id'] == 'Adverse Events':
        if pd.isna(row['Secondary_id']):

            row['primary_evidence'] = row['Primary Adverse Events']
            row['secondary_evidence'] = None
        else:

            row['primary_evidence'] = row['Primary Adverse Events']
            row['secondary_evidence'] = row['Secondary Adverse Events']

    else:
        pass
    return row


df = df.apply(set_evidence, axis=1)
dev = dev.apply(set_evidence, axis=1)
test = test.apply(set_evidence, axis=1)

In [13]:

df.drop(['Primary Interventions','Primary Eligibility','Primary Results',	'Primary Adverse Events','Secondary Interventions',	'Secondary Eligibility','Secondary Results','Secondary Adverse Events'],axis=1,inplace=True)
dev.drop(['Primary Interventions','Primary Eligibility','Primary Results',	'Primary Adverse Events','Secondary Interventions',	'Secondary Eligibility','Secondary Results','Secondary Adverse Events'],axis=1,inplace=True)
test.drop(['Primary Interventions','Primary Eligibility','Primary Results',	'Primary Adverse Events','Secondary Interventions',	'Secondary Eligibility','Secondary Results','Secondary Adverse Events'],axis=1,inplace=True)

In [14]:
df.insert(0, 'Index', df.index)
dev.insert(0, 'Index', dev.index)
test.insert(0, 'Index', test.index)

In [15]:

def to_lowercase_list(evidence_list):
  try:
    return [item.lower() for item in evidence_list]
  except:
    return None

df['primary_evidence'] = df['primary_evidence'].apply(to_lowercase_list)
df['secondary_evidence'] = df['secondary_evidence'].apply(to_lowercase_list)
dev['primary_evidence'] = dev['primary_evidence'].apply(to_lowercase_list)
dev['secondary_evidence'] = dev['secondary_evidence'].apply(to_lowercase_list)
test['primary_evidence'] = test['primary_evidence'].apply(to_lowercase_list)
test['secondary_evidence'] = test['secondary_evidence'].apply(to_lowercase_list)

In [16]:
def generate_instruction(row):

    if pd.isnull(row['Secondary_id']):
        premise = f"Primary trial evidence are {row['primary_evidence']}."
    else:
        premise = f"Primary trial evidence are {row['primary_evidence']} and Secondary trial evidence are {row['secondary_evidence']}."

    hypothesis = row['Statement']


    options = "OPTIONS:\nEntailment\nContradiction"


    instruction = f"{premise} Question: Does {hypothesis} align with the provided details? {options}"
    return instruction


df['Instruction'] = df.apply(generate_instruction, axis=1)
dev['Instruction'] = dev.apply(generate_instruction, axis=1)
test['Instruction'] = test.apply(generate_instruction, axis=1)

In [18]:
custom_stopwords=['a','an','the','are','it','what','which','who','whom','this',
                  'that','these','those','is','was', 'were', 'be', 'been', 'being',
                  'have', 'has', 'had', 'having','if', 'or','as', 'until',
                  'while', 'of', 'at', 'by', 'for', 'with', 'about',
                  'between', 'into', 'through', 'above',
                  'below','to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over',
                   'again','then', 'once', 'here', 'there', 'when',
                  'where', 'why', 'how', 'all','any', 'each',
                  'most', 'other', 'some', 'such', 'only','own', 'so', 'than',
                  'too', 'very', 's', 't', 'can', 'will', 'just', 'should', 'now','it','and','they','their','whereas']

In [19]:
def remove_custom_stop_words_list(evidence_list):
  try:
    return [' '.join([word for word in item.split() if word not in custom_stopwords]) for item in evidence_list]
  except:
    return None
df['primary_evidence'] = df['primary_evidence'].apply(remove_custom_stop_words_list)
df['secondary_evidence'] = df['secondary_evidence'].apply(remove_custom_stop_words_list)
dev['primary_evidence'] = dev['primary_evidence'].apply(remove_custom_stop_words_list)
dev['secondary_evidence'] = dev['secondary_evidence'].apply(remove_custom_stop_words_list)
test['primary_evidence'] = test['primary_evidence'].apply(remove_custom_stop_words_list)
test['secondary_evidence'] = test['secondary_evidence'].apply(remove_custom_stop_words_list)


In [21]:
train_t = df[['Instruction','Label']]
train_t.head(1)

Instruction  \
5bc844fc-e852-4270-bfaf-36ea9eface3d  Primary trial evidence are None and Secondary ...   

                                              Label  
5bc844fc-e852-4270-bfaf-36ea9eface3d  Contradiction

In [22]:
val_t = dev[['Instruction','Label']]
val_t.head(1)

Instruction  \
1adc970c-d433-44d0-aa09-d3834986f7a2  Primary trial evidence are ['outcome measureme...   

                                              Label  
1adc970c-d433-44d0-aa09-d3834986f7a2  Contradiction

In [23]:
def convert_labels(data):

  data['Label'] = data['Label'].apply(lambda x: 0 if x == 'Contradiction' else 1)
  return data


train_t = convert_labels(train_t)
val_t = convert_labels(val_t)

<ipython-input-23-ec8d5d17257a>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Label'] = data['Label'].apply(lambda x: 0 if x == 'Contradiction' else 1)
<ipython-input-23-ec8d5d17257a>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['Label'] = data['Label'].apply(lambda x: 0 if x == 'Contradiction' else 1)


In [26]:

def convert_to_dict(row):

    text = row['Instruction']
    Label = row['Label']


    formatted_entry = f'"text": "{text}","Label":{Label}'

    return formatted_entry

print('for train_t')
print('\n')


converted_entries_train_t = {}

for index, row in train_t.iterrows():

    converted_entries_train_t[index] = convert_to_dict(row)


for key, value in converted_entries_train_t.items():
    print(value)

print('--------------------------------------------------------------------------------')
print('for val_t')
print('\n')

converted_entries_val_t = {}

for index, row in val_t.iterrows():

    converted_entries_val_t[index] = convert_to_dict(row)


for key, value in converted_entries_val_t.items():
    print(value)


for train_t


"text": "Primary trial evidence are None and Secondary trial evidence are None. Question: Based on the information, would All the primary trial participants do not receive any oral capecitabine, oral lapatinib ditosylate or cixutumumab IV, in conrast all the secondary trial subjects receive these. be supported? OPTIONS:
Entailment
Contradiction","Label":0
"text": "Primary trial evidence are ['disease characteristics:', '  histologically or cytologically confirmed infiltrating breast cancer', '  clinical evidence of metastatic disease', '  measurable disease, defined as at least one measurable lesion per recist criteria', '  no non-measurable disease only, defined as all other lesions, including small lesions (longest diameter < 2 cm) and truly non-measurable lesions, including any of the following:', '  bone lesions', '  leptomeningeal disease', '  ascites', '  pleural/pericardial effusion', '  inflammatory breast disease', '  lymphangitis cutis/pulmonis', '  abdominal ma

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [28]:

train_t['converted_entries'] = [convert_to_dict(row) for index, row in train_t.iterrows()]


val_t['converted_entries'] = [convert_to_dict(row) for index, row in val_t.iterrows()]

train_t.head(1)


<ipython-input-28-88dd8061ba12>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_t['converted_entries'] = [convert_to_dict(row) for index, row in train_t.iterrows()]
<ipython-input-28-88dd8061ba12>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  val_t['converted_entries'] = [convert_to_dict(row) for index, row in val_t.iterrows()]


Instruction  \
5bc844fc-e852-4270-bfaf-36ea9eface3d  Primary trial evidence are None and Secondary ...   

                                      Label  \
5bc844fc-e852-4270-bfaf-36ea9eface3d      0   

                                                                      converted_entries  
5bc844fc-e852-4270-bfaf-36ea9eface3d  "text": "Primary trial evidence are None and S...

In [29]:
train_t.drop(['Instruction'],axis=1,inplace=True)
val_t.drop(['Instruction'],axis=1,inplace=True)

<ipython-input-29-a4289c9f19af>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_t.drop(['Instruction'],axis=1,inplace=True)
<ipython-input-29-a4289c9f19af>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  val_t.drop(['Instruction'],axis=1,inplace=True)


In [30]:
import pandas as pd
from datasets import Dataset
import random




train_df = pd.DataFrame(train_t)
test_df = pd.DataFrame(val_t)

train_df['Label'] = train_df['Label'].astype(str)
test_df['Label'] = test_df['Label'].astype(str)
train_t= Dataset.from_pandas(train_df)
val_t = Dataset.from_pandas(test_df)

In [33]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

model_id = "google/flan-t5-base"
tokenizer = AutoTokenizer.from_pretrained(model_id)


max_sequence_length = 2500
tokenizer.model_max_length = max_sequence_length


tokenized_inputs = train_t.map(lambda x: tokenizer(x["converted_entries"], truncation=True), batched=True, remove_columns=['converted_entries', 'Label'])
max_source_length = max([len(x) for x in tokenized_inputs["input_ids"]])
print(f"Max source length: {max_source_length}")


tokenized_targets = train_t.map(lambda x: tokenizer(x["Label"], truncation=True),batched=True, remove_columns=['converted_entries', 'Label'])
max_target_length = max([len(x) for x in tokenized_targets["input_ids"]])
print(f"Max target length: {max_target_length}")


/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Map:   0%|          | 0/1700 [00:00<?, ? examples/s]

Max source length: 2500


Map:   0%|          | 0/1700 [00:00<?, ? examples/s]

Max target length: 3


In [34]:
tokenized_inputs_v = val_t.map(lambda x: tokenizer(x["converted_entries"], truncation=True), batched=True, remove_columns=['converted_entries', 'Label'])
max_source_length_v = max([len(x) for x in tokenized_inputs_v["input_ids"]])
print(f"Max source length: {max_source_length_v}")
tokenized_targets_v = val_t.map(lambda x: tokenizer(x["Label"], truncation=True), batched=True, remove_columns=['converted_entries', 'Label'])
max_target_length_v = max([len(x) for x in tokenized_targets_v["input_ids"]])
print(f"Max target length: {max_target_length_v}")

Map:   0%|          | 0/200 [00:00<?, ? examples/s]

Max source length: 2500


Map:   0%|          | 0/200 [00:00<?, ? examples/s]

Max target length: 3


In [35]:
def preprocess_function(sample, padding="max_length"):

    inputs = [item for item in sample["converted_entries"]]


    model_inputs = tokenizer(inputs, max_length=max_source_length, padding=padding, truncation=True)

    labels = tokenizer(text_target=sample["Label"], max_length=max_target_length, padding=padding, truncation=True)

    if padding == "max_length":
        labels["input_ids"] = [
            [(l if l != tokenizer.pad_token_id else -100) for l in label] for label in labels["input_ids"]
        ]

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

tokenized_dataset_train_t = train_t.map(preprocess_function, batched=True, remove_columns=['converted_entries', 'Label'])
print(f"Keys of tokenized dataset: {list(tokenized_dataset_train_t.features)}")
tokenized_dataset_val_t = val_t.map(preprocess_function, batched=True, remove_columns=['converted_entries', 'Label'])
print(f"Keys of tokenized dataset: {list(tokenized_dataset_val_t.features)}")


Map:   0%|          | 0/1700 [00:00<?, ? examples/s]

Keys of tokenized dataset: ['__index_level_0__', 'input_ids', 'attention_mask', 'labels']


Map:   0%|          | 0/200 [00:00<?, ? examples/s]

Keys of tokenized dataset: ['__index_level_0__', 'input_ids', 'attention_mask', 'labels']


In [36]:
from transformers import AutoModelForSeq2SeqLM


model_id="google/flan-t5-base"


model = AutoModelForSeq2SeqLM.from_pretrained(model_id)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [37]:
import evaluate
import nltk
import numpy as np
from nltk.tokenize import sent_tokenize
nltk.download("punkt")
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

metric = evaluate.load("f1")


def postprocess_text(preds, labels):
    preds = [pred.strip() for pred in preds]
    labels = [label.strip() for label in labels]


    preds = ["\n".join(sent_tokenize(pred)) for pred in preds]
    labels = ["\n".join(sent_tokenize(label)) for label in labels]

    return preds, labels

def compute_metrics(eval_preds):
    preds, labels = eval_preds
    if isinstance(preds, tuple):
        preds = preds[0]
    decoded_preds = tokenizer.batch_decode(preds, skip_special_tokens=True)

    labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)

    decoded_preds, decoded_labels = postprocess_text(decoded_preds, decoded_labels)


    accuracy = accuracy_score(decoded_labels, decoded_preds)


    precision = precision_score(decoded_labels, decoded_preds, average='macro')
    recall = recall_score(decoded_labels, decoded_preds, average='macro')
    f1 = f1_score(decoded_labels, decoded_preds, average='macro')


    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in preds]
    gen_len = np.mean(prediction_lens)

    return {'accuracy': accuracy * 100, 'precision': precision * 100, 'recall': recall * 100, 'f1': f1 * 100, 'gen_len': gen_len}


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [38]:
from transformers import DataCollatorForSeq2Seq


label_pad_token_id = -100

data_collator = DataCollatorForSeq2Seq(
    tokenizer,
    model=model,
    label_pad_token_id=label_pad_token_id,
    pad_to_multiple_of=8
)

In [39]:
from huggingface_hub import HfFolder
from transformers import Seq2SeqTrainer, Seq2SeqTrainingArguments


training_args = Seq2SeqTrainingArguments(
    output_dir="./log_results",
    per_device_train_batch_size=3,
    per_device_eval_batch_size=2,
    predict_with_generate=True,
    fp16=False,
    learning_rate=1e-4,

    num_train_epochs=2,

    logging_dir='./logs',
    logging_strategy="epoch",

    evaluation_strategy="steps",
    save_strategy="epoch",
    save_total_limit=2,
    load_best_model_at_end =False,

)


trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=tokenized_dataset_train_t,
    eval_dataset=tokenized_dataset_val_t,
    compute_metrics=compute_metrics,
)

trainer.train()


/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1141: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1141: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


TrainOutput(global_step=1134, training_loss=0.013471976789847883, metrics={'train_runtime': 1070.0945, 'train_samples_per_second': 3.177, 'train_steps_per_second': 1.06, 'total_flos': 1.13862308511744e+16, 'train_loss': 0.013471976789847883, 'epoch': 2.0})

In [40]:
trainer.evaluate()

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1141: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


{'eval_loss': 0.009701580740511417,
 'eval_accuracy': 99.5,
 'eval_precision': 99.5049504950495,
 'eval_recall': 99.5,
 'eval_f1': 99.49998749968749,
 'eval_gen_len': 2.495,
 'eval_runtime': 45.6723,
 'eval_samples_per_second': 4.379,
 'eval_steps_per_second': 2.19,
 'epoch': 2.0}

In [41]:
model_path = "/content/fine_tune_b2_model.pth"
torch.save(model.state_dict(), model_path)



## testing model

In [42]:
test_t = test[['Instruction']]
test_t.head(1)

Instruction
47468741-3624-4321-90ee-1c680a293b25  Primary trial evidence are ['adverse events 1:...

In [43]:

def convert_test_dict(row):

    text = row['Instruction']


    formatted_entry = f'"text": "{text}"'

    return formatted_entry


converted_entries_test_t = {}

for index, row in test_t.iterrows():

    converted_entries_test_t[index] = convert_test_dict(row)


for key, value in converted_entries_test_t.items():
    print(value)

"text": "Primary trial evidence are ['adverse events 1:', '  total: 0/733 (0.00%)', 'adverse events 2:', '  total: 0/765 (0.00%)'] and Secondary trial evidence are ['adverse events 1:', '  total: 0/88 (0.00%)', 'adverse events 2:', '  total: 0/86 (0.00%)']. Question: Based on the information, would the record shows 5 total cases of asthenia and 3 total cases of pyrexia in the patients of the primary and secondary clinical trials. be supported? OPTIONS:
Entailment
Contradiction"
"text": "Primary trial evidence are ['inclusion criteria for dose escalation and expansion phase:', '  signed written informed consent', '  male or female participants aged greater than or equal to 18 years', '  participants must have histologically or cytologically proven metastatic or locally advanced solid tumors, for which no standard therapy exists or standard therapy has failed. availability of tumor archival material or fresh biopsies is optional for participants in dose escalation', '  eastern cooperativ

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [45]:
test_t['converted_entries'] = [convert_test_dict(row) for index, row in test_t.iterrows()]

test_t.head(1)

<ipython-input-45-8f8d0d9939e7>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_t['converted_entries'] = [convert_test_dict(row) for index, row in test_t.iterrows()]


Instruction  \
47468741-3624-4321-90ee-1c680a293b25  Primary trial evidence are ['adverse events 1:...   

                                                                      converted_entries  
47468741-3624-4321-90ee-1c680a293b25  "text": "Primary trial evidence are ['adverse ...

In [46]:
test_t.drop(['Instruction'],axis=1,inplace=True)

<ipython-input-46-425e2381bd88>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_t.drop(['Instruction'],axis=1,inplace=True)


In [47]:
test_f = pd.DataFrame(test_t)
test_t = Dataset.from_pandas(test_f)
test_t

Dataset({
    features: ['converted_entries', '__index_level_0__'],
    num_rows: 5500
})

In [48]:
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM
tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-base")


model.load_state_dict(torch.load(model_path))


/usr/local/lib/python3.10/dist-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


<All keys matched successfully>

In [49]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)

T5ForConditionalGeneration(
  (shared): Embedding(32128, 768)
  (encoder): T5Stack(
    (embed_tokens): Embedding(32128, 768)
    (block): ModuleList(
      (0): T5Block(
        (layer): ModuleList(
          (0): T5LayerSelfAttention(
            (SelfAttention): T5Attention(
              (q): Linear(in_features=768, out_features=768, bias=False)
              (k): Linear(in_features=768, out_features=768, bias=False)
              (v): Linear(in_features=768, out_features=768, bias=False)
              (o): Linear(in_features=768, out_features=768, bias=False)
              (relative_attention_bias): Embedding(32, 12)
            )
            (layer_norm): T5LayerNorm()
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (1): T5LayerFF(
            (DenseReluDense): T5DenseGatedActDense(
              (wi_0): Linear(in_features=768, out_features=2048, bias=False)
              (wi_1): Linear(in_features=768, out_features=2048, bias=False)
              (wo):

In [50]:
from tqdm.auto import tqdm

samples_number = len(test_t)
progress_bar = tqdm(range(samples_number))
predictions_list = []

for i in range(samples_number):
  text = test_t['converted_entries'][i]
  inputs = tokenizer.encode_plus(text, padding='max_length', max_length=2500, return_tensors='pt').to(device)
  outputs = model.generate(inputs['input_ids'], attention_mask=inputs['attention_mask'], max_length=20, num_beams=4, early_stopping=True)
  prediction = tokenizer.decode(outputs[0], skip_special_tokens=True)
  predictions_list.append(prediction)
  progress_bar.update(1)


  0%|          | 0/5500 [00:00<?, ?it/s]

In [51]:
print(predictions_list)

['0', '1', '1', '1', '0', '1', '1', '1', '0', '0', '1', '1', '1', '0', '0', '1', '1', '0', '1', '1', '0', '0', '0', '0', '0', '1', '1', '1', '1', '1', '1', '1', '1', '0', '1', '1', '1', '0', '0', '0', '0', '0', '1', '0', '1', '1', '1', '1', '1', '1', '1', '0', '1', '0', '1', '0', '0', '0', '0', '0', '0', '0', '1', '0', '0', '1', '0', '0', '1', '1', '1', '0', '0', '1', '1', '0', '0', '0', '1', '1', '1', '1', '1', '1', '0', '0', '1', '1', '0', '1', '0', '0', '0', '1', '1', '0', '0', '0', '0', '1', 'None', '0', '1', '0', '1', '0', '0', '0', '1', '0', '0', '1', '1', '1', '0', '1', '0', '0', '1', '0', '0', '0', '1', '1', '1', '1', '1', '0', '0', '0', '1', '1', '0', '1', '0', '1', 'None', '1', '1', '1', '1', '1', '0', '1', '1', '1', '1', '1', '1', '1', '1', '0', '0', '0', '1', '0', '1', '1', '1', 'None', '1', '0', '1', 'None', '0', '1', 'None', '0', '1', '0', '1', '1', '0', '1', '1', '0', '0', '0', '0', '0', '0', '0', '0', '1', '1', '0', '1', '1', '0', 'None', '0', '1', '1', '1', '0', '1', '

In [53]:
prediction_list = ["Entailment" if x== '1' else "Contradiction" for x in predictions_list]
prediction_list

['Contradiction',
 'Entailment',
 'Entailment',
 'Entailment',
 'Contradiction',
 'Entailment',
 'Entailment',
 'Entailment',
 'Contradiction',
 'Contradiction',
 'Entailment',
 'Entailment',
 'Entailment',
 'Contradiction',
 'Contradiction',
 'Entailment',
 'Entailment',
 'Contradiction',
 'Entailment',
 'Entailment',
 'Contradiction',
 'Contradiction',
 'Contradiction',
 'Contradiction',
 'Contradiction',
 'Entailment',
 'Entailment',
 'Entailment',
 'Entailment',
 'Entailment',
 'Entailment',
 'Entailment',
 'Entailment',
 'Contradiction',
 'Entailment',
 'Entailment',
 'Entailment',
 'Contradiction',
 'Contradiction',
 'Contradiction',
 'Contradiction',
 'Contradiction',
 'Entailment',
 'Contradiction',
 'Entailment',
 'Entailment',
 'Entailment',
 'Entailment',
 'Entailment',
 'Entailment',
 'Entailment',
 'Contradiction',
 'Entailment',
 'Contradiction',
 'Entailment',
 'Contradiction',
 'Contradiction',
 'Contradiction',
 'Contradiction',
 'Contradiction',
 'Contradiction',
 'Co

In [55]:
import pandas as pd

test_pred = pd.DataFrame({"prediction": prediction_list})


test_pred.insert(0, 'Index', test.index)





In [57]:
output_dict = {}
for index, row in test_pred.iterrows():
    output_dict[row['Index']] = {"Prediction": row['prediction']}
print(output_dict)

{'47468741-3624-4321-90ee-1c680a293b25': {'Prediction': 'Contradiction'}, '93e6ed2b-1e3f-4cbe-a49e-cbc74b31e1aa': {'Prediction': 'Entailment'}, 'ad9fe1aa-9798-4c53-ab23-23ac2924918c': {'Prediction': 'Entailment'}, 'cdcb40f6-994c-4085-869a-dab87e67ba04': {'Prediction': 'Entailment'}, '7df66c3f-de87-4542-9797-06325684db65': {'Prediction': 'Contradiction'}, '3ce48a99-7310-4a2f-8853-e46db55af26e': {'Prediction': 'Entailment'}, '9349c7c8-7771-4dfc-8981-3c8d84ac5236': {'Prediction': 'Entailment'}, 'e25a03fa-f51c-4c0d-b737-375a968ce6be': {'Prediction': 'Entailment'}, '5c5a882c-4840-4e2e-83f8-341283caa359': {'Prediction': 'Contradiction'}, 'a06166e6-12c9-49ba-ad3a-7fcfb5234174': {'Prediction': 'Contradiction'}, 'adb18104-31a9-4eef-817b-0ab742bd4093': {'Prediction': 'Entailment'}, 'feca3829-9b38-4738-8bad-e8a0fcf9029f': {'Prediction': 'Entailment'}, '0471ee43-16a7-417e-94db-0ef86bd5b0a9': {'Prediction': 'Entailment'}, '74b96ae6-3e1a-4f1c-bbf0-a79ed0e4ee75': {'Prediction': 'Contradiction'}, '14e

In [58]:
import json
file_path = "resultsf4.json"

with open(file_path, "w") as json_file:
    json.dump(output_dict, json_file)

print("Data successfully written to", file_path)

Data successfully written to resultsf3.json
